In [262]:
import numpy as np
import pandas as pd
import seaborn as sns
from h3 import h3
import folium
from geojson import Feature, Point, FeatureCollection
import json
import matplotlib
import plotly.express as px
from shapely.geometry import Polygon



In [263]:
def visualize_hexagons(hexagons, color="red", folium_map=None):
    """
    hexagons is a list of hexcluster. Each hexcluster is a list of hexagons. 
    eg. [[hex1, hex2], [hex3, hex4]]
    """
    polylines = []
    lat = []
    lng = []
    for hex in hexagons:
        polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
        # flatten polygons into loops.
        outlines = [loop for polygon in polygons for loop in polygon]
        polyline = [outline + [outline[0]] for outline in outlines][0]
        lat.extend(map(lambda v:v[0],polyline))
        lng.extend(map(lambda v:v[1],polyline))
        polylines.append(polyline)
    
    if folium_map is None:
        m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
    else:
        m = folium_map
    for polyline in polylines:
        my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color=color)
        m.add_child(my_PolyLine)
    return m
    

def visualize_polygon(polyline, color):
    polyline.append(polyline[0])
    lat = [p[0] for p in polyline]
    lng = [p[1] for p in polyline]
    m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
    my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color=color)
    m.add_child(my_PolyLine)
    return m

In [264]:
h3_address = h3.geo_to_h3(46.94747523446262, 7.436766375275757, 8) # lat, lng, hex resolution                                                                                                        
m = visualize_hexagons([h3_address])
display(m)

https://medium.com/analytics-vidhya/how-to-create-a-choropleth-map-using-uber-h3-plotly-python-458f51593548

In [265]:
#path = f"D:\Private copy\passagierfrequenz.csv"
path = f"/Users/labor/Desktop/Private/passagierfrequenz.csv"

Data_pre = pd.read_csv(path, delimiter= ";")
Data_pre = Data_pre.drop(columns= [ "Bezugsjahr", "Eigner", "DWV", "DNWV", "Bemerkung", "Bemerkungen","Bemerkungen.1", "Note", "lod"])
Geopos = Data_pre["Geoposition"].str.split(pat ="," ,expand=True)#
Geopos = Geopos.rename(columns = {0: "y", 1: "x"})
Data = pd.concat([Data_pre, Geopos], axis=1).drop(columns = ["Geoposition"])
Data.x = Data.x.astype(float)
Data.y = Data.y.astype(float)
Data["DTV_log"] = np.log(Data.DTV)
Data.head(4)

code Bahnhof_Haltestelle Kanton      DTV          y         x    DTV_log
0   AD              Aadorf     TG   1700.0  47.488118  8.903301   7.438384
1   AA               Aarau     AG  37900.0  47.391360  8.051274  10.542706
2  ABO   Aarburg-Oftringen     AG   2500.0  47.320268  7.908223   7.824046
3  AAT              Aathal     ZH    740.0  47.335959  8.765625   6.606650

In [266]:
H3_res = 7
def geo_to_h3(row):
        return h3.geo_to_h3(lat=row.y,lng=row.x,resolution = H3_res)

        

def add_geometry(row):
  points = h3.h3_to_geo_boundary(row['h3_cell'], True)
  
  return Polygon(points)

def hexagons_dataframe_to_geojson(df_hex, hex_id_field,geometry_field, value_field, name_field,file_output = None):

    list_features = []

    for i, row in df_hex.iterrows():
        feature = Feature(geometry = row[geometry_field],
                          id = row[hex_id_field],
                          properties = {"value": row[value_field]},
                          name = row[name_field])
        list_features.append(feature)

    feat_collection = FeatureCollection(list_features)

    if file_output is not None:
        with open(file_output, "w") as f:
            json.dump(feat_collection, f)

    else :
      return feat_collection


def get_color(custom_cm, val, vmin, vmax):
    return matplotlib.colors.to_hex(custom_cm((val-vmin)/(vmax-vmin)))
def choropleth_map(df_aggreg, column_name = "value", border_color = 'white', fill_opacity = 0.7, color_map_name = "Blues", initial_map = None):
    
    """
    Creates choropleth maps given the aggregated data. initial_map can be an existing map to draw on top of.
    """    
    #colormap
    min_value = df_aggreg[column_name].min()
    max_value = df_aggreg[column_name].max()
    mean_value = df_aggreg[column_name].mean()
    print(f"Colour column min value {min_value}, max value {max_value}, mean value {mean_value}")
    print(f"Hexagon cell count: {df_aggreg['hex_id'].nunique()}")
    
    # the name of the layer just needs to be unique, put something silly there for now:
    name_layer = "Choropleth " + str(df_aggreg)
    
    if initial_map is None:
        initial_map = folium.Map(location= [47, 4], zoom_start=5.5, tiles="cartodbpositron")

    #create geojson data from dataframe
    geojson_data = hexagons_dataframe_to_geojson(df_hex = df_aggreg, column_name = column_name)

    # color_map_name 'Blues' for now, many more at https://matplotlib.org/stable/tutorials/colors/colormaps.html to choose from!
    custom_cm = matplotlib.cm.get_cmap(color_map_name)

    folium.GeoJson(
        geojson_data,
        style_function=lambda feature: {
            'fillColor': get_color(custom_cm, feature['properties'][column_name], vmin=min_value, vmax=max_value),
            'color': border_color,
            'weight': 1,
            'fillOpacity': fill_opacity 
        }, 
        name = name_layer
    ).add_to(initial_map)

    return initial_map

In [267]:
Data['h3_cell'] = Data.apply(geo_to_h3,axis=1)
Data = Data.drop(index = Data[Data["h3_cell"]== "0"].index)
Data['geometry'] = Data.apply(add_geometry,axis=1)


In [268]:
geojson_obj_bhf = (hexagons_dataframe_to_geojson
                (Data,
                 hex_id_field='h3_cell',
                 value_field='DTV_log',
                 geometry_field='geometry',
                 name_field= "Bahnhof_Haltestelle"))

https://plotly.com/python/colorscales/

In [281]:
Data[Data["Bahnhof_Haltestelle"]== "Zürich HB"]

code Bahnhof_Haltestelle Kanton       DTV          y         x    DTV_log  \
896  ZUE           Zürich HB     ZH  423600.0  47.378177  8.540212  12.956545   

             h3_cell                                           geometry  
896  871f8ed95ffffff  POLYGON ((8.528697143693117 47.383052181729255...

In [269]:
fig = (px.choropleth_mapbox(
                    Data, 
                    geojson=geojson_obj_bhf, 
                    locations='h3_cell', 
                    color=Data["DTV_log"],
                    hover_name = Data["Bahnhof_Haltestelle"],
                    color_continuous_scale="turbo",
                    range_color=(0,Data["DTV_log"].max()),                 
                    mapbox_style='carto-positron',
                    zoom=9,
                    center = {"lat": 47.41609409868053, "lon": 8.553879741076177},
                    opacity=0.7,
                    labels={'count':'# of fire ignitions '}))
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [270]:
AWK_locs = { "Zürich": [47.416109048074674, 8.553933383336904], "Bern": [46.94749533405075, 7.436754099592461], "Basel": [47.54836037511811, 7.589188599288886], "Lausanne": [46.51634822675881, 6.634604712129138] }
AWK_stao = pd.DataFrame.from_dict(AWK_locs).transpose().rename(columns = {0: "y", 1: "x"})
AWK_stao

In [272]:
#path = f"D:\Private copy\mobilitat.csv"
path = f"/Users/labor/Desktop/Private/mobilitat.csv"

Data_serv = pd.read_csv(path, delimiter= ";")

Data_serv = Data_serv[Data_serv.parkrail_anzahl.notna()]
Data_serv_useful = Data_serv[["parkrail_anzahl", "Abkuerzung Bahnhof", "Geoposition" ]]
Data_serv_useful
Geopos_2 = Data_serv_useful["Geoposition"].str.split(pat ="," ,expand=True)#
Geopos_2 = Geopos_2.rename(columns = {0: "y", 1: "x"})
Data_serv_useful = pd.concat([Data_serv_useful, Geopos_2], axis=1).drop(columns = ["Geoposition"])
Data_serv_useful.x = Data_serv_useful.x.astype(float)
Data_serv_useful.y = Data_serv_useful.y.astype(float)
Data_serv_useful['h3_cell'] = Data_serv_useful.apply(geo_to_h3,axis=1)
Data_serv_useful = Data_serv_useful.drop(index = Data_serv_useful[Data_serv_useful["h3_cell"]== "0"].index)
Data_serv_useful


parkrail_anzahl Abkuerzung Bahnhof          y         x          h3_cell
33              31.0                 MU  47.533591  7.647894  871f83802ffffff
34              58.0                 PR  47.522669  7.690817  871f8381dffffff
35              25.0                FRE  47.501470  7.719111  871f83819ffffff
36             203.0                LST  47.484461  7.731367  871f838e6ffffff
37              18.0                LSN  47.470345  7.759763  871f838e2ffffff
..               ...                ...        ...       ...              ...
816             50.0                LBD  47.104825  8.373760  871f83202ffffff
817              8.0               BNWD  46.967826  7.465478  871f83553ffffff
818              8.0               BNWD  46.967826  7.465478  871f83553ffffff
820             22.0               ZGSE  47.173725  8.507242  871f83274ffffff
821            165.0               MELH  47.428075  8.276363  871f83a1bffffff

[593 rows x 5 columns]

In [273]:
radius = 6

Data_g = Data[["h3_cell", "DTV_log"]].groupby(by = "h3_cell").mean()
stationdict = Data_g.to_dict()
stationdict = stationdict["DTV_log"]
stationinfluence = {}
for center_hex in stationdict:
    for i in range(0,radius):
        ring = h3.hex_ring(center_hex, i)
        for ring_hex in ring:
           stationinfluence[ring_hex] = 0
    #stationinfluence[center_hex] = stationdict[center_hex]
for center_hex in stationdict:
    for i in range(0,radius):
        ring = h3.hex_ring(center_hex, i)
        for ring_hex in ring:
            stationinfluence[ring_hex] += np.sqrt(stationdict[center_hex ])/((i+1))**2

            

Data_pg = Data_serv_useful[["h3_cell", "parkrail_anzahl"]].groupby(by= "h3_cell").sum()
parkdict = Data_pg.to_dict()
parkdict = parkdict["parkrail_anzahl"]
parkinfluence = {}
for center_hex in parkdict:
    for i in range(0,radius):
        ring = h3.hex_ring(center_hex, i)
        for ring_hex in ring:
           parkinfluence[ring_hex] = 0
    #parkinfluence[center_hex]= parkdict[center_hex]
for center_hex in parkdict:
    for i in range(0,radius):
        ring = h3.hex_ring(center_hex, i)
        for ring_hex in ring:
            parkinfluence[ring_hex] += np.sqrt(parkdict[center_hex ])/((i+1))**2


In [274]:
station_df = pd.DataFrame.from_dict(stationinfluence, orient="index")
parking_df = pd.DataFrame.from_dict(parkinfluence, orient= "index")
Totaldf = station_df.join(parking_df, how = "outer" , lsuffix = "station_usage", rsuffix = "parking_usage").rename(columns = {"0station_usage": "station_usage", "0parking_usage": "parking_usage"}).fillna(0)
Totaldf_norm = (Totaldf / Totaldf.mean()) -Totaldf.std()
Totaldf_norm["Bilanz"] = Totaldf_norm["station_usage"]-Totaldf_norm["parking_usage"]
Totaldf_norm = Totaldf_norm.reset_index(level= 0).rename(columns={"index": "h3_cell"})


Totaldf_norm.head()
#Totaldf_norm = Totaldf_norm.drop(index = Totaldf_norm[Totaldf_norm["h3_cell"]== "0"].index)

h3_cell  station_usage  parking_usage    Bilanz
0  871f80610ffffff      -1.643857      -4.031065  2.387207
1  871f80611ffffff      -1.643857      -4.031065  2.387207
2  871f80612ffffff      -1.591048      -4.011044  2.419996
3  871f80613ffffff      -1.591048      -4.011044  2.419996
4  871f80616ffffff      -1.643857      -4.031065  2.387207

In [275]:
Totaldf_norm[Totaldf_norm["h3_cell"]== "871f83646ffffff"]

h3_cell  station_usage  parking_usage    Bilanz
1967  871f83646ffffff       0.803205      -4.076566  4.879771

In [276]:
Totaldf_norm['geometry'] = Totaldf_norm.apply(add_geometry,axis=1)
geojson_obj_bil = (hexagons_dataframe_to_geojson
                (Totaldf_norm,
                 hex_id_field='h3_cell',
                 value_field='Bilanz',
                 geometry_field='geometry',
                 name_field= "h3_cell"))

In [277]:
fig_2 = (px.choropleth_mapbox(
                    Totaldf_norm, 
                    geojson=geojson_obj_bil, 
                    locations='h3_cell', 
                    color=Totaldf_norm["Bilanz"],
                    hover_name = Totaldf_norm["Bilanz"],
                    color_continuous_scale="turbo",
                    range_color=(-6,Totaldf_norm["Bilanz"].max()),                 
                    mapbox_style='carto-positron',
                    zoom=9,
                    center = {"lat": 47.41609409868053, "lon": 8.553879741076177},
                    opacity=0.6,
                    labels={"Public Park'n'ride compared to daily station usage"}))
fig_2.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.update_layout(
    title_text="Public Park'n'ride compared to daily station usage")

fig_2.show()

In [312]:
Data_scatterplot[Data_scatterplot["code"]== "ZUE"]

code Kanton       DTV  parkrail_anzahl
963  ZUE     ZH  423600.0              0.0

In [324]:
Data_station_scatter = Data[["code", "Kanton", "DTV"]]
Data_parking_scatter = Data_serv_useful[["parkrail_anzahl"	,"Abkuerzung Bahnhof"]].rename(columns={"Abkuerzung Bahnhof": "code"})

Data_scatterplot = Data_station_scatter.merge(Data_parking_scatter, how = "outer", on = "code", ).fillna(0)
#pd.concat([Data_station_scatter, Data_parking_scatter], axis = 1, )
#Data_scatterplot = Data_scatterplot.set_index("code")
#Data_scatterplot = Data_scatterplot[Data_scatterplot["code"]== "ZUE"]
fig = px.scatter(Data_scatterplot, x = "DTV", y = "parkrail_anzahl", hover_data=["code"] , color="Kanton" , log_x = True, 
                 
                 )
fig.update_layout(
    title_text="Scatter plot between usage of the station and park'n'ride availability.")
fig.show()